# Synthetic data generation
First, the [Kaggle dataset Handwritten math symbols](https://www.kaggle.com/datasets/xainano/handwrittenmathsymbols?resource=download) dataset will be used as it has a friendly file structure that is pretty easy to work with. 

In [6]:
import numpy as np
from skimage import io
from skimage.color import rgb2gray
from skimage.transform import resize,rescale
from skimage.util import invert
import os

read_path="./extracted_images/"
label_names=['0', '1', '2', '3', '4', '5', '6', '7', '8', '9', #Digits
             '-', '+', '=','/','#div','#times','#pm',                                #Operators
             'a', 'b', 'c','d','e','f','g','h','i','j','k','l','m','n','o','p','q','r','s','t','u','v','w','x','y','z',#Alphabetical lowercase
            #  'A', 'B', 'C','D','E','F','G','H','I','J','K','L','M','N','O','P','Q','R','S','T','U','V','W','X','Y','Z',#Alphabetical uppercase
             '#alpha','#beta','#delta','#gamma','#lambda','#mu','#phi','#pi','#sigma','#theta',
             '#sin','#cos','#tan',                  #trigonometric functions
             '#log','#sqrt',                  #Algebra common functions
             '#gt','#lt','#geq','#leq','#neq', #Inequalities
             '(',')','[',']','#{','#}',#Brackets
             '!','#in','#exists','#forall','#infty','#rightarrow'#symbols
             ]
label_names_index=dict()

for idx,label in enumerate(label_names):
  label_names_index[label]=idx

label_names_index

{'0': 0,
 '1': 1,
 '2': 2,
 '3': 3,
 '4': 4,
 '5': 5,
 '6': 6,
 '7': 7,
 '8': 8,
 '9': 9,
 '-': 10,
 '+': 11,
 '=': 12,
 '/': 13,
 '#div': 14,
 '#times': 15,
 '#pm': 16,
 'a': 17,
 'b': 18,
 'c': 19,
 'd': 20,
 'e': 21,
 'f': 22,
 'g': 23,
 'h': 24,
 'i': 25,
 'j': 26,
 'k': 27,
 'l': 28,
 'm': 29,
 'n': 30,
 'o': 31,
 'p': 32,
 'q': 33,
 'r': 34,
 's': 35,
 't': 36,
 'u': 37,
 'v': 38,
 'w': 39,
 'x': 40,
 'y': 41,
 'z': 42,
 '#alpha': 43,
 '#beta': 44,
 '#delta': 45,
 '#gamma': 46,
 '#lambda': 47,
 '#mu': 48,
 '#phi': 49,
 '#pi': 50,
 '#sigma': 51,
 '#theta': 52,
 '#sin': 53,
 '#cos': 54,
 '#tan': 55,
 '#log': 56,
 '#sqrt': 57,
 '#gt': 58,
 '#lt': 59,
 '#geq': 60,
 '#leq': 61,
 '#neq': 62,
 '(': 63,
 ')': 64,
 '[': 65,
 ']': 66,
 '#{': 67,
 '#}': 68,
 '!': 69,
 '#in': 70,
 '#exists': 71,
 '#forall': 72,
 '#infty': 73,
 '#rightarrow': 74}

In [157]:
#Diccionario que almacena las direcciones de todas las imágenes de cada caracter
dir_dict=dict()
for key in label_names_index:
  key=key.strip("#")
  if(key=="/"):
    dir_dict[key]=os.listdir(read_path+"forward_slash")
  else:
    dir_dict[key]=os.listdir(read_path+key)

In [6]:
A=[1,2,3]
4 in A

False

In [205]:
def categorize_char(sym_char):
  if(sym_char in ['#frac','^','_']):
    return "special"
  if(label_names_index[sym_char]<10):
    return "digit"
  if(label_names_index[sym_char]<17):
    return "operator"
  if(label_names_index[sym_char]<53):
    return "char"
  if(label_names_index[sym_char]<58):
    return "function"
  if(label_names_index[sym_char]<63):
    return "inequality"
  if(label_names_index[sym_char]<69):
    return "brackets"
  if(label_names_index[sym_char]<75):
    return "symbols"

def draw_char(img,el,categ,X,index=0):
    el=el.strip("#")
    choice=np.random.randint(len(dir_dict[el]))
    if(el=="/"):
      els="forward_slash"
    else:
      els=el
    sym_img=rgb2gray(io.imread(read_path+els+"/"+dir_dict[el][choice]))
    if(categ in ['digit','char','brackets','symbols']):
      WIDTH=30+np.random.randint(-7,7)
      HEIGHT=90+np.random.randint(-10,10)
      Y=(img.shape[0]-HEIGHT)//2+np.random.randint(-5,5)

    else:
      WIDTH=20+np.random.randint(-5,5)
      HEIGHT=20+np.random.randint(-5,5)
      Y=(img.shape[0]-HEIGHT)//2+np.random.randint(-5,5)
    sym_img=resize(sym_img,(HEIGHT,WIDTH))
    # print(X,Y,HEIGHT,WIDTH)

    img[Y:Y+HEIGHT,X:X+WIDTH]+=invert(sym_img)
    bounding_box={
        'xmin':X,
        'xmax':X+WIDTH,
        'ymin':Y,
        'ymax':Y+HEIGHT,
        'class':el
    }
    padding=WIDTH+10+np.random.randint(-5,5)
    
    return img,padding,bounding_box


def generate_image(list_struct,IMG_SIZE=(128,720)):
  img=np.zeros(IMG_SIZE)
  bounding_boxes=[]
  X=10
  i=0
  while(i<len(list_struct)):
    el=list_struct[i]
    categ=categorize_char(el)
    if(categ=="special"):
      if(el=="#frac"):
        img,padding,bounding_box=draw_fraction(img,list_struct[i+1],list_struct[i+2],X)
        bounding_boxes=bounding_boxes+bounding_box
        X+=padding
        i+=3
        continue
    if(categ=="function"):
      img,padding,bounding_box=draw_function(img,el,list_struct[i+1],X)
      bounding_boxes=bounding_boxes+bounding_box
      X+=padding
      i+=2
      continue
    
    img,padding,bounding_box=draw_char(img,el,categ,X)

    bounding_boxes.append(bounding_box)
    X+=padding
    i+=1


  # for el in list_struct:
  #   if(el=="#frac"):
  #     img,padding,bounding_boxes=draw_fraction()
  #   categ=categorize_char(el)
  #   img,padding,bounding_box=draw_char(img,el,categ,X)
  #   bounding_boxes.append(bounding_box)
  #   X+=padding
  #   """
  #   if(categ=='digit' or categ=='var'):
  #     X+=70
  #   else:
  #     X+=40
  #   """
  return img, bounding_boxes,X

def draw_fraction(img,num,den,X):
  bounding_boxes=[]
  #NUM
  num_img,bounding_boxes_num,X_num=generate_image(num)
  num_img=num_img[:,:X_num]
  num_img=rescale(num_img,0.4)
  bounding_boxes.append(bounding_boxes_num)
  num_H,num_W=num_img.shape

  #DEN
  den_img,bounding_boxes_den,X_den=generate_image(den)
  den_img=den_img[:,:X_den]
  den_img=rescale(den_img,0.4)
  bounding_boxes.append(bounding_boxes_den)
  den_H,den_W=den_img.shape

  #FRACTION WIDTH
  frac_W=max(num_W,den_W)+np.random.randint(5,10)
  #FRACTION BAR
  el="-"
  choice=np.random.randint(len(dir_dict[el]))
  fr_BAR=rgb2gray(io.imread(read_path+el+"/"+dir_dict[el][choice]))
  fr_BAR=resize(fr_BAR,(fr_BAR.shape[0],frac_W))
  fr_BAR=invert(fr_BAR)
  
  #DRAW NUM
  X_num=(frac_W-num_W)//2+X
  Y_num=np.random.randint(5,15)
  img[Y_num:Y_num+num_H,X_num:X_num+num_W]+=num_img

  #DRAW DEN
  X_den=(frac_W-den_W)//2+X
  Y_den=Y_num+num_H+np.random.randint(5,10)
  img[Y_den:Y_den+den_H,X_den:X_den+den_W]+=den_img
  
  #DRAW FRACTION BAR
  BARH,BARW=fr_BAR.shape
  Y_BAR=Y_num+num_H+np.random.randint(-15,-5)
  X_BAR=X
  img[Y_BAR:Y_BAR+BARH,X_BAR:X_BAR+BARW]+=fr_BAR

  padding=frac_W+10+np.random.randint(-5,5)

  return img,padding,bounding_boxes

def draw_function(img,func,argument,X):
  argument_image,bounding_box,X_argument=generate_image(argument)
  argument_image=argument_image[:,:X_argument]
  argument_image=rescale(argument_image,0.6)
  padding=0
  if(func=="#sqrt"):
    #DRAW SQRT
    el="sqrt"
    choice=np.random.randint(len(dir_dict[el]))
    sqrt_img=rgb2gray(io.imread(read_path+el+"/"+dir_dict[el][choice]))
    
    HEIGHT1=90+np.random.randint(0,20)
    WIDTH1=argument_image.shape[1]+np.random.randint(5,15)
    Y=(img.shape[0]-HEIGHT1)//2+np.random.randint(0,2)
    sqrt_img=resize(sqrt_img,(HEIGHT1,WIDTH1))
    img[Y:Y+HEIGHT1,X:X+WIDTH1]+=invert(sqrt_img)

    #DRAW ARGUMENT
    X+=np.random.randint(5,15)
    Y+=np.random.randint(10,20)
    HEIGHT2,WIDTH2=argument_image.shape
    img[Y:Y+HEIGHT2,X:X+WIDTH2]+=argument_image 
    
    padding=WIDTH1+np.random.randint(5,15)
  else:
    el=func.strip("#")
    choice=np.random.randint(len(dir_dict[el]))
    func_img=rgb2gray(io.imread(read_path+el+"/"+dir_dict[el][choice]))
    OR_H,OR_W=func_img.shape
    HEIGHT1=90+np.random.randint(-10,10)
    WIDTH1=OR_W*(HEIGHT1//OR_H)
    NEW_SHAPE=(HEIGHT1,WIDTH1)

    func_img=invert(resize(func_img,NEW_SHAPE))

    Y1=(img.shape[0]-HEIGHT1)//2+np.random.randint(-5,5)
    img[Y1:Y1+HEIGHT1,X:X+WIDTH1]+=func_img

    X+=WIDTH1+np.random.randint(2,10)
    HEIGHT2,WIDTH2=argument_image.shape
    Y2=(img.shape[0]-HEIGHT2)//2+np.random.randint(-5,5)
    img[Y2:Y2+HEIGHT2,X:X+WIDTH2]+=argument_image

    padding=WIDTH1+WIDTH2+np.random.randint(5,15)


    
  return img,padding,bounding_box
    







In [ ]:
ge

# Brief example

In [144]:
from matplotlib import pyplot as plt
import json
# struct=['(','#rightarrow','-','b','+','c',')','=','5','y']
struct=['#frac',['a','+','b'],'2','+','#log','2','#neq','5','x']
y={}
for i in range(10):
    ex,bounding_boxes,_=generate_image(struct)
    fname=f"imagen{i}.png"
    y[fname]=bounding_boxes
    io.imsave(f"prueba/"+fname,ex)

with open('prueba/data.json','w') as fp:
    json.dump(y,fp)


<ipython-input-143-f3978fcc80bc>:23: FutureWarning: The behavior of rgb2gray will change in scikit-image 0.19. Currently, rgb2gray allows 2D grayscale image to be passed as inputs and leaves them unmodified as outputs. Starting from version 0.19, 2D arrays will be treated as 1D images with 3 channels.
  sym_img=rgb2gray(io.imread(read_path+el+"/"+dir_dict[el][choice]))
<ipython-input-143-f3978fcc80bc>:112: FutureWarning: The behavior of rgb2gray will change in scikit-image 0.19. Currently, rgb2gray allows 2D grayscale image to be passed as inputs and leaves them unmodified as outputs. Starting from version 0.19, 2D arrays will be treated as 1D images with 3 channels.
  fr_BAR=rgb2gray(io.imread(read_path+el+"/"+dir_dict[el][choice]))
<ipython-input-143-f3978fcc80bc>:163: FutureWarning: The behavior of rgb2gray will change in scikit-image 0.19. Currently, rgb2gray allows 2D grayscale image to be passed as inputs and leaves them unmodified as outputs. Starting from version 0.19, 2D array

['_100052.jpg',
 '_100601.jpg',
 '_101042.jpg',
 '_101724.jpg',
 '_102081.jpg',
 '_102995.jpg',
 '_103114.jpg',
 '_1033.jpg',
 '_104049.jpg',
 '_105116.jpg',
 '_105453.jpg',
 '_105461.jpg',
 '_107014.jpg',
 '_107022.jpg',
 '_107098.jpg',
 '_107106.jpg',
 '_107566.jpg',
 '_107574.jpg',
 '_107682.jpg',
 '_107690.jpg',
 '_108991.jpg',
 '_108999.jpg',
 '_109749.jpg',
 '_109757.jpg',
 '_109819.jpg',
 '_109827.jpg',
 '_109930.jpg',
 '_109938.jpg',
 '_110851.jpg',
 '_110859.jpg',
 '_111044.jpg',
 '_111052.jpg',
 '_111566.jpg',
 '_111718.jpg',
 '_111726.jpg',
 '_111977.jpg',
 '_112485.jpg',
 '_112543.jpg',
 '_112551.jpg',
 '_112695.jpg',
 '_113227.jpg',
 '_113443.jpg',
 '_113656.jpg',
 '_38447.jpg',
 '_39003.jpg',
 '_39005.jpg',
 '_39042.jpg',
 '_39160.jpg',
 '_39162.jpg',
 '_39295.jpg',
 '_39801.jpg',
 '_39848.jpg',
 '_40205.jpg',
 '_40220.jpg',
 '_40603.jpg',
 '_40831.jpg',
 '_40836.jpg',
 '_40870.jpg',
 '_40895.jpg',
 '_41065.jpg',
 '_41072.jpg',
 '_41077.jpg',
 '_41421.jpg',
 '_41479.jpg',

In [216]:
for i in range(10000):
    a=generate_random_structure()
    print(a)
    ex,bounding_boxes,_=generate_image(a)
    print(i)




['#frac', ['#rightarrow', '4', '#pi', '#times', '2', 'w'], ['7', '#theta', '#times', '4', '#pi']]
0
['#log', ['[', '#rightarrow', 'h', '/', 'j', ']'], '-', '#infty', '#gt', '#infty']
1
['#frac', ['7', 'r'], ['8', '#times', '#infty'], '/', '#infty', '#pm', '#gamma', '=', '#infty']


<ipython-input-205-b95d6fa43e0f>:26: FutureWarning: The behavior of rgb2gray will change in scikit-image 0.19. Currently, rgb2gray allows 2D grayscale image to be passed as inputs and leaves them unmodified as outputs. Starting from version 0.19, 2D arrays will be treated as 1D images with 3 channels.
  sym_img=rgb2gray(io.imread(read_path+els+"/"+dir_dict[el][choice]))
<ipython-input-205-b95d6fa43e0f>:117: FutureWarning: The behavior of rgb2gray will change in scikit-image 0.19. Currently, rgb2gray allows 2D grayscale image to be passed as inputs and leaves them unmodified as outputs. Starting from version 0.19, 2D arrays will be treated as 1D images with 3 channels.
  fr_BAR=rgb2gray(io.imread(read_path+el+"/"+dir_dict[el][choice]))
<ipython-input-205-b95d6fa43e0f>:168: FutureWarning: The behavior of rgb2gray will change in scikit-image 0.19. Currently, rgb2gray allows 2D grayscale image to be passed as inputs and leaves them unmodified as outputs. Starting from version 0.19, 2D arra

2
['#forall', 'p', '#leq', '5', '#exists', 'g', '#gt', '5']
3
['#rightarrow', '#sqrt', ['[', '#rightarrow', '1', 'j', ']'], '/', 'c', '/', 'h']
4
['3', '+', '4', '#theta', '=', 'j']
5
['#forall', 'e', '#gt', '3', '#forall', 'm', '=', '5', '#forall', '#gamma', '#lt', '7']
6
['#rightarrow', '#log', ['(', '#rightarrow', '#infty', ')'], '#geq', '#infty']


<ipython-input-205-b95d6fa43e0f>:150: FutureWarning: The behavior of rgb2gray will change in scikit-image 0.19. Currently, rgb2gray allows 2D grayscale image to be passed as inputs and leaves them unmodified as outputs. Starting from version 0.19, 2D arrays will be treated as 1D images with 3 channels.
  sqrt_img=rgb2gray(io.imread(read_path+el+"/"+dir_dict[el][choice]))


7
['#tan', ['#{', '#rightarrow', '8', '#div', '#infty', '#}'], '+', '3', '#lt', '#infty']
8
['#infty', '/', '#infty', '#div', '#infty']
9
['#exists', '#lambda', '=', '1', '#forall', 'f', '#leq', '6', '#forall', 'a', '#gt', '3']
10
['#forall', 'e', '#leq', '4', '#exists', '#gamma', '#in', '1', '#exists', 't', '#lt', '6']
11
['#sin', ['(', '5', '#gamma', ')'], '#times', '#beta', '/', '#infty']
12
['#forall', 'w', '#lt', '6', '#forall', 'q', '#in', '2']
13
['#infty', '#gt', '#sin', ['#{', '#rightarrow', '#infty', '#pm', 'q', '#}']]
14
['#frac', ['#infty'], ['#rightarrow', '1', '#pm', '4', 'd']]
15
['#infty', '#gt', '#log', ['[', '5', '-', 'c', ']']]
16
['#frac', ['#infty', '/', '#infty'], ['6', 'r'], '#neq', 'd']
17
['#rightarrow', '#cos', ['(', '7', '+', '4', ')'], '#div', 'd', '=', '7']
18
['3', '/', '4']
19
['#frac', ['#infty'], ['4'], '/', 'i', '+', '#infty']
20
['#forall', 'b', '=', '4']
21
['#exists', 'h', '#in', '1']
22
['#rightarrow', '#frac', ['#rightarrow', '1', '#mu'], ['q', '/

In [241]:
def generate_random_structure(kind=None,nfraq=0,nfunc=0,inside=False):
    struct=[]
    if(kind==None):
        choices=["eq","ineq","conj"]
        choice_kind=np.random.randint(3)
        kind=choices[choice_kind]
    if(kind in ["eq","ineq"]):
        if(np.random.randint(1,10)<=2):
            struct.append("#rightarrow")
        if(nfraq==0 and not inside):
            nels_left=np.random.randint(1,4)
            nels_right=np.random.randint(0,3)
        else:
            nels_left=np.random.randint(1,3)
            nels_right=0
        #left
        for i in range(nels_left):
            #el: number, var, var with coeff,(var: alph, greek), function, infty,  fraq 
            if(nfraq<1 and nfunc<1 and not inside):
                kind_el=np.random.randint(1,7)
            else:
                kind_el=np.random.randint(1,5)

            if(kind_el==1):#number
                number=str(np.random.randint(1,9))
                for digit in number:
                    struct.append(digit)
            elif(kind_el==2):#var
                var=np.random.randint(17,53)
                struct.append(label_names[var])
            elif(kind_el==3):#varwithcoeff
                coeff=str(np.random.randint(1,9))
                for digit in coeff:
                    struct.append(digit)
                var=np.random.randint(17,53)
                struct.append(label_names[var])
            elif(kind_el==4):
                struct.append("#infty")
            elif(kind_el==5):
                func=np.random.randint(53,58)
                struct.append(label_names[func])
                inside_function=generate_random_structure(kind="eq",inside=True,nfunc=nfunc+1)
                brackets=np.random.randint(32,35)
                inside_function=[label_names[2*brackets-1]]+inside_function+[label_names[2*brackets]]
                struct.append(inside_function)
                nfunc+=1
            elif(kind_el==6):
                struct.append("#frac")
                num=generate_random_structure("eq",nfraq=nfraq+1)
                den=generate_random_structure("eq",nfraq=nfraq+1)
                struct.append(num)
                struct.append(den)
                nfraq+=1
                
            if(i!=nels_left-1):
                op=np.random.randint(10,17)
                if(op==12):
                    op+=1
                struct.append(label_names[op])
        if(nels_right>0):
            comp=np.random.randint(57,63)
            if(comp==57):
                comp=12
            struct.append(label_names[comp])
            if(nfraq<1 and nfunc<1 and not inside):
                kind_el=np.random.randint(1,7)
            else:
                kind_el=np.random.randint(1,5)

            if(kind_el==1):#number
                number=str(np.random.randint(1,9))
                for digit in number:
                    struct.append(digit)
            elif(kind_el==2):#var
                var=np.random.randint(17,53)
                struct.append(label_names[var])
            elif(kind_el==3):#varwithcoeff
                coeff=str(np.random.randint(1,9))
                for digit in coeff:
                    struct.append(digit)
                var=np.random.randint(17,53)
                struct.append(label_names[var])
            elif(kind_el==4):
                struct.append("#infty")
            elif(kind_el==5):
                func=np.random.randint(53,58)
                struct.append(label_names[func])
                inside_function=generate_random_structure(kind="eq",inside=True,nfunc=nfunc+1)
                brackets=np.random.randint(32,35)
                inside_function=[label_names[2*brackets-1]]+inside_function+[label_names[2*brackets]]
                struct.append(inside_function)
                nfunc+=1
            elif(kind_el==6):
                struct.append("#frac")
                num=generate_random_structure("eq",nfraq=nfraq+1)
                den=generate_random_structure("eq",nfraq=nfraq+1)
                struct.append(num)
                struct.append(den)
                nfraq+=1                  
            if(i!=nels_left-1):
                op=np.random.randint(10,17)
                if(op==12):
                    op+=1
                struct.append(label_names[op])
    elif(kind=="conj"):
        nels=np.random.randint(1,4)
        for i in range(nels):
            symbol=["#forall","#exists"][np.random.randint(0,2)]
            var=label_names[np.random.randint(17,53)]
            op=(["=","#in"]+label_names[58:64])[np.random.randint(0,6)]
            num=str(np.random.randint(1,9))
            struct.append(symbol)
            struct.append(var)
            struct.append(op)
            for digit in num:
                struct.append(digit)
    return struct
    

def list_to_tex(struct):
    tex=""
    i=0
    while(i<len(struct)):
        el=struct[i]
        categ=categorize_char(el)
        if(categ in ["special","function"]):
            if(el=="#frac"):
                tex+=el+"{"+list_to_tex(struct[i+1])+"}"+"{"+list_to_tex(struct[i+2])+"}"
                i+=2
            else:
                tex+=el+"{"+list_to_tex(struct[i+1])+"}"
                i+=1
        else:
            if(el=="/"):
                el="#division"
            tex+=el
        if(i!=len(struct)-1):
            tex+=" "
        i+=1

    return tex

def generate_dataset(directory,cant=100000):
    y={}
    for i in range(cant):
        filename="im"+str(i).zfill(int(np.floor(np.log10(cant))+1))+"_"
        struct=generate_random_structure()
        filename+=list_to_tex(struct)+".png"
        ex,bounding_boxes,_=generate_image(struct)
        y[filename]=bounding_boxes
        print(directory+"/"+filename)
        io.imsave(directory+"/"+filename,ex)
    with open(directory+'/data.json','w') as fp:
        json.dump(y,fp)
        


In [243]:
directory="./data_gen"
generate_dataset(directory,100000)

<ipython-input-205-b95d6fa43e0f>:26: FutureWarning: The behavior of rgb2gray will change in scikit-image 0.19. Currently, rgb2gray allows 2D grayscale image to be passed as inputs and leaves them unmodified as outputs. Starting from version 0.19, 2D arrays will be treated as 1D images with 3 channels.
  sym_img=rgb2gray(io.imread(read_path+els+"/"+dir_dict[el][choice]))
Lossy conversion from float64 to uint8. Range [0, 1]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float64 to uint8. Range [0, 1]. Convert image to uint8 prior to saving to suppress this warning.


./data_gen/im000000_#forall #theta #lt 1 #exists r #gt 7.png
./data_gen/im000001_#forall #phi #leq 7 #forall #delta #leq 1 #exists k #lt 4.png


<ipython-input-205-b95d6fa43e0f>:168: FutureWarning: The behavior of rgb2gray will change in scikit-image 0.19. Currently, rgb2gray allows 2D grayscale image to be passed as inputs and leaves them unmodified as outputs. Starting from version 0.19, 2D arrays will be treated as 1D images with 3 channels.
  func_img=rgb2gray(io.imread(read_path+el+"/"+dir_dict[el][choice]))
Lossy conversion from float64 to uint8. Range [0, 1]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float64 to uint8. Range [0, 1]. Convert image to uint8 prior to saving to suppress this warning.


./data_gen/im000002_4 #lt #sin{#{ 6 + 3 z #}}.png
./data_gen/im000003_#forall d #geq 1 #forall m #in 3 #exists #delta #geq 4.png


<ipython-input-205-b95d6fa43e0f>:117: FutureWarning: The behavior of rgb2gray will change in scikit-image 0.19. Currently, rgb2gray allows 2D grayscale image to be passed as inputs and leaves them unmodified as outputs. Starting from version 0.19, 2D arrays will be treated as 1D images with 3 channels.
  fr_BAR=rgb2gray(io.imread(read_path+el+"/"+dir_dict[el][choice]))
Lossy conversion from float64 to uint8. Range [0, 1]. Convert image to uint8 prior to saving to suppress this warning.
<ipython-input-241-38479f6a8e82>:152: UserWarning: ./data_gen/im000005_#exists c #geq 7.png is a low contrast image
  io.imsave(directory+"/"+filename,ex)
Lossy conversion from float64 to uint8. Range [0, 1]. Convert image to uint8 prior to saving to suppress this warning.
Lossy conversion from float64 to uint8. Range [0, 1]. Convert image to uint8 prior to saving to suppress this warning.


...


./data_gen/im013579_#rightarrow 7 #geq #infty.png
./data_gen/im013580_p.png
./data_gen/im013581_#frac{2 #div 7 #delta}{#rightarrow #lambda} #div 1 #neq #infty.png


Lossy conversion from float64 to uint8. Range [0, 1]. Convert image to uint8 prior to saving to suppress this warning.


./data_gen/im013582_#rightarrow 6 #div #frac{#infty}{#rightarrow #infty} #pm 1.png


<ipython-input-241-38479f6a8e82>:152: UserWarning: ./data_gen/im013583_#exists #lambda #gt 8.png is a low contrast image
  io.imsave(directory+"/"+filename,ex)
Lossy conversion from float64 to uint8. Range [0, 1]. Convert image to uint8 prior to saving to suppress this warning.


./data_gen/im013583_#exists #lambda #gt 8.png


In [220]:
a=["#frac","1","2","+","#sin",["(","#pi",")"],"#leq","5"]
list_to_tex(a)

'#frac{1}{2} + #sin{( #pi )} #leq 5'

In [230]:
int(np.floor(np.log10(100000))+1)

6

# Dataset structure

`imXXXXXX_<LATEX_FORMULA>.png`

In another file, `boundering_boxes.json`, the symbols boundering boxes data are stored.